In [100]:
import email.parser 

import os, sys, stat
import chardet
import pickle
from bs4 import BeautifulSoup
from pprint import pprint


In [101]:
filename = "TRAINING/TRAIN_00016.eml"

if not os.path.exists(filename): # dest path doesnot exist
    print("ERROR: input file does not exist:", filename)
    os.exit(1)

f = open(filename)

msg = email.message_from_file(f)

# Subject, to and from fields
sub = msg.get('subject')
sub = str(sub)
to = str(msg.get('to'))
fr = str(msg.get('from'))

# get header of message
# parser = email.parser.HeaderParser()
# headers = parser.parsestr(msg.as_string())


# get body of message
payload = msg.get_payload()
if type(payload) == type(list()) :
    payload = payload[0] # only use the first part of payload
if type(payload) != type('') :
    payload = str(payload)

# decoded_message = ''
charset = chardet.detect(payload)['encoding']

{"charset": charset, "payload": payload}


('ERROR: input file does not exist:', 'EXTRACT_TRAINING/TRAIN_00016.eml')


AttributeError: 'module' object has no attribute 'exit'

In [95]:
def ExtractSubPayload (filename):
    ''' Extract the subject and payload from the .eml file.

    '''
    if not os.path.exists(filename): # dest path doesnot exist
        print("ERROR: input file does not exist:", filename)
        os.exit(1)

    f = open(filename)

    msg = email.message_from_file(f)

    # Subject, to and from fields
    sub = msg.get('subject')
    sub = str(sub)
    to = str(msg.get('to'))
    fr = str(msg.get('from'))
    
    # get header of message
    parser = email.parser.HeaderParser()
    headers = parser.parsestr(msg.as_string())
    
    # get body of message
    payload = msg.get_payload()
    if type(payload) == type(list()) :
        payload = payload[0] # only use the first part of payload
    if type(payload) != type('') :
        payload = str(payload)

    # decoded_message = ''
    charset = chardet.detect(payload)['encoding']

    return {"charset": charset, "payload": payload}

In [86]:
ExtractSubPayload("TRAINING/TRAIN_00016.eml")

{'charset': 'ISO-8859-2',
 'headers': <email.message.Message instance at 0x7fb5d3ee98c0>,
 'payload': ">I'd normally never buy this but the Xbox is Eur300 on IOL's shop, a very\n>large company are making a loss on it and:\n>\n>http://xbox-linux.sourceforge.net/articles.php?aid=1&sub=Press%20Release%3A%20Xbox%20Linux%20Mandrake%209%20Released\n>\n>Mandrake has been released for it.\n\nisn't it \xa4250 in Smyths?\n\ndon't forget to add to that the modchip, and the time to put it on.\n\n(/me thinks unless you want 3d graphics, www.mini-itx.com is the way to go :))\n\nL.\n-- \nIrish Linux Users' Group: ilug@linux.ie\nhttp://www.linux.ie/mailman/listinfo/ilug for (un)subscription information.\nList maintainer: listmaster@linux.ie\n\n\n"}

In [87]:
trainDict = {}

with open("SPAMTrain.label") as f:
    for line in f:
#         print(line[2:])
        isSpam = int(line[0])
        filename = line[2:]
        trainDict[filename.strip()] = isSpam
        

# print trainDict
x = 0
for mail in trainDict:
    res = ExtractSubPayload("TRAINING/"+mail) 
#     print res['filename']
#     print mail
    res["isSpam"] = trainDict[mail]
    trainDict[mail] = res
    if(x %1000 == 0):
        print x
    x+=1
    


0
1000
2000
3000
4000


In [88]:
with open("emailData.pickle", "w") as f:
    pickle.dump(trainDict, f)

In [59]:
with open("emailData.pickle", "rb") as f:
    trainDict = pickle.load(f)

In [89]:
trainDict

{'TRAIN_00525.eml': {'charset': 'ascii',
  'headers': <email.message.Message instance at 0x7fb5d3f40200>,
  'isSpam': 1,
  'payload': "From nobody Sat May  7 16:44:03 2016\nContent-Type: text/plain; charset=ISO-8859-1\n\n@Merciadri Luca\r\n\r\n[quote]\r\nI have no answer to your question, but I am wondering... what does 'lol'\r\nmean here? Is it some version of something, or did you simply put this over\r\nthere because you have some sense of humor and you like to make your\r\n(somewhat old) config appear less depressing to the others' eyes?\r\n[/quote]\r\n\r\n\r\n... it's the hostname, but it is funny! I don't give a damn about what\r\nothers might think anyway, I'm just having fun with it, making some tests,\r\npushing my knowledge...\r\n\r\n@Stefan\r\n\r\n[quote]\r\n486 will work.  686 may work.\r\n[/quote]\r\n\r\n\r\nMy impression exactly, but I'd like to be sure : if I scrape this install,\r\nI'll have a hard time recovering it...\r\n\r\n@Bob\r\n\r\n[quote]\r\nionreflex@lol:~$ cat

In [90]:
# Get all payloads for word freqs
payloads = []
for mail in trainDict:
    payloads.append(trainDict[mail]['payload'])
    
payloads

["From nobody Sat May  7 16:44:03 2016\nContent-Type: text/plain; charset=ISO-8859-1\n\n@Merciadri Luca\r\n\r\n[quote]\r\nI have no answer to your question, but I am wondering... what does 'lol'\r\nmean here? Is it some version of something, or did you simply put this over\r\nthere because you have some sense of humor and you like to make your\r\n(somewhat old) config appear less depressing to the others' eyes?\r\n[/quote]\r\n\r\n\r\n... it's the hostname, but it is funny! I don't give a damn about what\r\nothers might think anyway, I'm just having fun with it, making some tests,\r\npushing my knowledge...\r\n\r\n@Stefan\r\n\r\n[quote]\r\n486 will work.  686 may work.\r\n[/quote]\r\n\r\n\r\nMy impression exactly, but I'd like to be sure : if I scrape this install,\r\nI'll have a hard time recovering it...\r\n\r\n@Bob\r\n\r\n[quote]\r\nionreflex@lol:~$ cat /proc/cpuinfo\r\nprocessor: 0\r\nvendor_id: GenuineIntel\r\ncpu family: 5\r\nmodel: 4\r\nmodel name: Pentium MMX\r\nstepping: 4\r\nc